### Обработка исходных данных

In [455]:
import csv

edges = []
with open('/Users/ORomanov/Downloads/University/DM/jupyter/lab3/vk_links.csv') as file:
    for edge in csv.reader(file, delimiter=','):
        edges.append(edge)
    print('rm: ' + str(edges[0]))
    edges = edges[1:]
    
vertices = []
for edge in edges:
    vertices.append(edge[0])
    vertices.append(edge[1])

vertices = set(vertices)
vertices = list(vertices)

print('#E: ' + str(len(edges)))
print('#V: ' + str(len(vertices)))

rm: ['out_f', 'in_f']
#E: 16017
#V: 491


### Определим опции для отрисовки графа

In [456]:
visual_style = {}

visual_style["vertex_size"] = 5

visual_style["bbox"] = (600, 500)

visual_style["edge_arrow_size"] = 0.25
visual_style["edge_arrow_width"] = 0.25
visual_style["edge_width"] = 0.05
visual_style["edge_curved"] = 0.5

### Создадим граф

In [457]:
import igraph

graph = igraph.Graph()
graph.add_vertices(vertices)
graph.add_edges(edges)

igraph.plot(graph, **visual_style)

### Выделим сообщества с помощью библиотеки

In [458]:
vertexClustering = graph.community_label_propagation()
igraph.plot(vertexClustering, **visual_style)

### Реализуем поиск PageRank

In [459]:
class PageRanker:
    def __init__(self, graph):
        self.graph = graph
        
    def find(self):
        self.__set_initial_pagerank()
        self.__pagerank()
        self.__sort()
        
    def __pagerank(self):
        new_ranks = self.graph.vs["pagerank"]
        for vertex in self.graph.vs:
            rank_sum = 0.0
            for incoming_node in vertex.neighbors(mode=igraph.IN):
                numerator = incoming_node["pagerank"]
                denominator = len(incoming_node.neighbors(mode=igraph.OUT))
                transfer_amount = numerator / denominator
                
                new_ranks[incoming_node.index] = new_ranks[incoming_node.index] - transfer_amount
                rank_sum += transfer_amount
                
            new_ranks[vertex.index] = vertex["pagerank"] + rank_sum
            
        self.graph.vs["pagerank"] = new_ranks
        
    def __set_initial_pagerank(self):
        initial_pagerank = 1.0/len(self.graph.vs["name"])
        for vertex in self.graph.vs:
            vertex["pagerank"] = initial_pagerank
            
    def __sort(self):
        vertices = []
        for vertex in self.graph.vs:
            vertices.append((vertex["name"], vertex["pagerank"]))
        
        vertices.sort(key=lambda vertex: vertex[1], reverse=True)
        
        names = []
        pageranks = []
        for vertex in vertices:
            names.append(vertex[0])
            pageranks.append(vertex[1])
            
        self.graph.vs["name"] = names
        self.graph.vs["pagerank"] = pageranks

### Разобьем узлы в каждом выделенном сообществе на категории

In [460]:
def find_rank(length):
    result = []
    leader = 0.01 * length
    agent = 0.4 * length
    for i in range(length):
        if i == 0 or i < leader:
            result.append("leader")
        elif i < agent:
            result.append("agent")
        else:
            result.append("follower")
    return result

communities = []
for i in range(len(vertexClustering)): 
    communities.append(vertexClustering.subgraph(i)) 
    
for community in communities:
    pr = PageRanker(community)
    pr.find()
    community.vs["rank"] = find_rank(len(community.vs))

### Запишем ответ

In [461]:
with open('out.csv', mode='w', newline='') as out_file:
    writer = csv.writer(out_file, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
    writer.writerow(['User', 'Community_ID', 'User_type'])
    for community_id, community in enumerate(communities):
        for vertex in community.vs:
            writer.writerow([vertex["name"], community_id, vertex["rank"]])